In [118]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import Span
from shapely.geometry import Point
import geopandas as gpd
import glob
import bokeh
from datetime import datetime
from bokeh.layouts import column
from bokeh.models import Legend, Tabs, TabPanel
from bokeh.core.validation.warnings import MISSING_RENDERERS, EMPTY_LAYOUT

# Set fonts for matplotlib
plt.rcParams["font.family"] = "Arial"
plt.rcParams["font.size"] = 14

In [119]:

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(EMPTY_LAYOUT, True)

{Warning(code=1002, name='EMPTY_LAYOUT', description='Layout has no children')}

In [120]:
# Function to convert a pandas dataframe to a geopandas dataframe
def convert_to_gdf(df):
    geometry = [Point(xy) for xy in zip(df.longitude, df.latitude)]
    gdf = gpd.GeoDataFrame(df, crs="EPSG:4326", geometry=geometry)

    return gdf

# India – Floods and Extreme Weather Events

For this analysis, multiple events are utilized to capture the impact of distinct flood and weather-related shocks across India in 2024:

**1. Monsoon Season Studies Dataset (May Events)**  
These datasets contain daily data for two monsoon-related studies conducted in **May 2024**.  
- **Event 1 Baseline:** Pending to ask Meta  
- **Event 2 Baseline:** Pending to ask Meta 

**2. Cyclone Remal Business Activity Trends Dataset**  
This dataset captures the impact of **Cyclone Remal**, with daily data from **May 27th, 2024 to June 10th, 2024**.  
- **Baseline date:** April 12, 2024  (Pending to ask Meta )

**3. Landslides in Kerala Dataset**  
This dataset captures the impact of landslides during the **July–August 2024** period in Kerala.  (key date: 30 July 2024)
- **Baseline date:** Pending to ask Meta  

**4. Flooding Dataset (August–September)**  
This dataset captures flood-related disruptions from **August 25th to September 5th, 2024**.  
- **Baseline date:** Pending to ask Meta  

**5. Tropical Cyclone Dana Post**  
This dataset captures the business activity trends following **Tropical Cyclone Dana**, covering the **October–November 2024** period.  (Cyclone date:  24-25 October)
- **Baseline date:** Pending to ask Meta  

**6. Cyclone Fengal Dataset**  
This dataset covers the impact of **Cyclone Fengal** in **December 2024**, with daily data from **December 2nd to December 16th, 2024**.  (Cyclone date: Nov 25, 2024 – Dec 4,2024)
- **Baseline date:** October 18, 2024  

## Purpose of this Notebook

This notebook demonstrates the following analyses:

- **Visualizing Business Activity Data by Vertical for the National Population:**  
  Assessing how different business sectors were impacted during and after each crisis period.

- **Analyzing Changes in Business Activity by Region and Vertical:**  
  Exploring how business activity varied across Indian states and districts (Admin 2), with breakdowns by sector.


In [121]:
# Read shapefiles from HdX UNOCHA

#https://data.humdata.org/dataset/geoboundaries-admin-boundaries-for-india

ind_adm2 = gpd.read_file(
    "../../data/geoBoundaries-IND-ADM2-all/geoBoundaries-IND-ADM2.shp"
)
ind_adm1 = gpd.read_file(
    "../../data/geoBoundaries-IND-ADM1-all/geoBoundaries-IND-ADM1.shp"
)


### Data Information Summary

This dataset provides insights into business activity at the [GADM 2](https://gadm.org/) level, covering xx districts in India. 

#### **Activity Quantile (activity_quantile):**
The activity quantile metric is used to measure changes in Business Activity.

- **Purpose:** Measures changes in business activity relative to a baseline period.  
- **Key Values:**
  - **0.5:** Normal activity (baseline level).  
  - **Above 0.5:** Increased activity.  
  - **Below 0.5:** Decreased activity.  

#### **Calculation Overview:**
1. Compare daily activity of business pages to their baseline activity levels (quantiles).  
2. Aggregate and standardize these values to follow a normal distribution.  
3. Apply a cumulative probability transformation to derive a value between **0 and 1**.  
4. Average results over 7 days to reduce daily noise.  
5. Provides equal weight to all businesses, avoiding bias from more active pages. 


In [122]:
businessActivity2024 = pd.read_csv("../../data/business-activity-trends/raw/bangladesh-india-sri_lanka-business-activity-trends-crisis-20240509-20241216.csv")

businessActivity2024 = businessActivity2024[businessActivity2024["country"] == "IND"]


In [123]:
# Convert columns to datetime

businessActivity2024["ds"] = businessActivity2024["ds"].apply(
    lambda x: pd.to_datetime(x)
)


In [124]:
import unicodedata

# Rename columns from shapefile to match activity data
ind_adm2 = ind_adm2.rename(columns={"shapeName": "polygon_name"})
ind_adm2["polygon_name"] = ind_adm2["polygon_name"].str.upper()

# Rename columns from flood data to match activity data
businessActivity2024 = businessActivity2024.rename(columns={"Admin2": "polygon_name"})
businessActivity2024["polygon_name"] = businessActivity2024["polygon_name"].str.upper()

In [125]:
# Get the unique business verticals 
business_verticals = list(businessActivity2024["business_vertical"].unique())

print(
    f"India's Floods Business Actvity Trends has the following business verticals {business_verticals}"
)

India's Floods Business Actvity Trends has the following business verticals ['Travel', 'Business & Utility Services', 'Local Events', 'Public Good', 'Retail', nan, 'Grocery & Convenience Stores', 'Lifestyle Services', 'Home Services', 'All', 'Professional Services', 'Manufacturing', 'Restaurants']


In [126]:
event_date_ranges = {
    "Monsoon_Study": ("2024-05-09", "2024-05-26"),
    "Cyclone_Remal": ("2024-05-25", "2024-06-10"),
    "Landslides_Kerala": ("2024-07-25", "2024-08-10"),
    "Flooding_Aug_Sept": ("2024-08-10", "2024-09-30"),
    "Cyclone_Dana": ("2024-10-20", "2024-11-13"),
    "Cyclone_Fengal": ("2024-12-02", "2024-12-16")
}

#  filtered datasets from the full business activity dataset
event_dataframes = {}
for event, (start, end) in event_date_ranges.items():
    mask = (businessActivity2024['ds'] >= pd.to_datetime(start)) & (businessActivity2024['ds'] <= pd.to_datetime(end))
    event_dataframes[event] = businessActivity2024[mask].copy()

# filtered and total (country-level mean) data to globals
for event_name, df in event_dataframes.items():
    globals()[f"businessActivity2024_{event_name}"] = df

    df_total = (
        df.groupby(["country", "business_vertical", "ds"], as_index=False)
        .mean(numeric_only=True)[["country", "business_vertical", "ds", "activity_quantile"]]
    )
    globals()[f"businessActivity2024_{event_name}_total"] = df_total


In [127]:
# pengding to add 

# read flood related data

import geopandas as gpd

flood_fgb_path = "../../data/flood/raw/eastbgd_floods_202408_20241024155022.pmtiles.flooded_area.fgb"
flooded_gdf = gpd.read_file(flood_fgb_path)

# read csv remal
# data downloaded from: UNOSTAT : https://unosat-rm.cern.ch/FloodAI/apps/BGD/?activation=AI20240502BGD
remal_flood = pd.read_csv("../../data/flood/raw/PopulationExposed_2024-05-24_TO_2024-05-29.csv")
# read csv flood
august_flood = pd.read_csv("../../data/flood/raw/PopulationExposed_2024-08-23_TO_2024-08-29.csv")

# compute flood percentage in both datasets

# Calculate the Flood Percentage
remal_flood["Flood_Percentage"] = (remal_flood["Flooded_Area_SqKM"] / remal_flood["Observed_Area_SqKM"]) * 100

# Standardize the Admin2 column for merging (strip spaces and convert to uppercase)
remal_flood["Admin2"] = remal_flood["Admin2"].str.strip().str.upper()

august_flood["Flood_Percentage"] = (august_flood["Flooded_Area_SqKM"] / august_flood["Observed_Area_SqKM"]) * 100

# Standardize the Admin2 column for merging (strip spaces and convert to uppercase)
august_flood["Admin2"] = august_flood["Admin2"].str.strip().str.upper()






In [128]:
from bokeh.models import Div, Span, Label
from bokeh.layouts import column

def get_line_plot(
    businessActivity,
    title,
    source,
    subtitle=None,
    vertical_dates=None,
    vertical_labels=None,
    limitations_note=None,  # Add note parameter
    label_offset=10  # Offset for labels to the right
):
    # Create the main figure
    p2 = figure(
        x_axis_type="datetime", 
        width=1000, 
        height=600, 
        toolbar_location="above",
        sizing_mode="stretch_width"  
    )
    p2.add_layout(Legend(), "right")

    # Define a color palette 
    from bokeh.palettes import Category20
    color_palette = Category20[15]  

    # Plot lines for each business vertical
    for id, business_vertical in enumerate(businessActivity["business_vertical"].unique()):
        if pd.isnull(business_vertical):  # Handle missing values in business_vertical
            business_vertical = "Unknown"

        business_vertical = str(business_vertical)  # Ensure it's a string

        df = businessActivity[businessActivity["business_vertical"] == business_vertical][
            ["ds", "activity_quantile"]
        ].reset_index(drop=True)

        p2.line(
            df["ds"],
            df["activity_quantile"],
            line_width=2,
            line_color=color_palette[id % len(color_palette)],  # Handle color overflow
            legend_label=business_vertical,
        )

    # Configure legend
    p2.legend.click_policy = "hide"
    p2.legend.label_text_font_size = "10pt"

    # Horizontal line at 0.5
    baseline = Span(
        location=0.5, 
        dimension="width", 
        line_color="black", 
        line_dash="dashed", 
        line_width=2
    )
    p2.add_layout(baseline)

    # Add vertical lines and labels if provided
    if vertical_dates and vertical_labels:
        for date, label_text in zip(vertical_dates, vertical_labels):
            vline = Span(location=date.timestamp() * 1000, 
                         dimension="height", 
                         line_color="grey", 
                         line_width=1.5, 
                         line_dash="dashed")
            
            p2.add_layout(vline)
            
            label = Label(
                x=date.timestamp() * 1000 + label_offset,  # Adjust to the right
                y=0.7,  # Example y position, adjust as needed
                text=label_text,
                text_color="grey",
                text_font_size="7pt"
            )
            p2.add_layout(label)

    # Use Div for title and subtitle
    title_div = Div(
        text=f"<h2>{title}</h2>", 
        styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"}
    )
    subtitle_div = Div(
        text=f"<p><em>{subtitle}</em></p>" if subtitle else "",
        styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"}
    )
    source_div = Div(
        text=f"<p><small>{source}</small></p>",
        styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"}
    )

    # Add limitations note if provided
    note_div = None
    if limitations_note:
        note_div = Div(
            text=f"""
            <div style="
                background-color: #f9f9f9; 
                border: 1px solid #dddddd; 
                padding: 10px; 
                border-radius: 5px;
                font-size: 12pt;
                margin-top: 10px;
                max-width: 800px;  /* Limit the width of the note */
                word-wrap: break-word;  /* Ensure text wraps within the width */
            ">
                <strong>Note:</strong> {limitations_note}
            </div>
            """,
        )

    # Combine all elements
    layout_elements = [title_div, subtitle_div, p2, source_div]
    if note_div:
        layout_elements.append(note_div)

    layout = column(*layout_elements)

    return layout




### 📊 Analysis by Business Vertical

This section explores how different **business sectors** were impacted during each crisis event.

In [129]:
from datetime import datetime
from bokeh.models import Div, TabPanel, Tabs
from bokeh.layouts import column
from bokeh.plotting import output_notebook, show

output_notebook()

# Redefine date ranges
event_date_ranges = {
    "Monsoon_Study": ("2024-05-09", "2024-05-26"),
    "Cyclone_Remal": ("2024-05-24", "2024-06-10"),
    "Landslides_Kerala": ("2024-07-25", "2024-08-10"),
    "Flooding_Aug_Sept": ("2024-08-10", "2024-09-30"),
    "Cyclone_Dana": ("2024-10-20", "2024-11-13"),
    "Cyclone_Fengal": ("2024-11-25", "2024-12-16"),
}

# Custom friendly titles for each event
title_map = {
    "Monsoon_Study": "Monsoon Study",
    "Cyclone_Remal": "Cyclone Remal",
    "Landslides_Kerala": "Landslides Kerala",
    "Flooding_Aug_Sept": "Flooding Aug–Sept",
    "Cyclone_Dana": "Cyclone Dana",
    "Cyclone_Fengal": "Cyclone Fengal",
}

# Optional: special subtitle/vertical markers by event
vertical_date_labels = {
    "Cyclone_Remal": {
        "dates": [datetime(2024, 5, 25), datetime(2024, 5, 28)],
        "labels": ["Cyclone Landfall", "Peak Impact"]
    },
    "Landslides_Kerala": {
        "dates": [datetime(2024, 7, 30)],
        "labels": ["Severe Landslide"]
    },
    "Cyclone_Dana": {
        "dates": [datetime(2024, 10, 25), datetime(2024, 10, 29)],
        "labels": ["Cyclone Landfall", "Peak Winds"]
    },
    "Cyclone_Fengal": {
        "dates": [datetime(2024, 11, 25), datetime(2024, 12, 4)],
        "labels": ["Cyclone Start", "Peak Impact"]
    }
}

tabs = []

for name in event_date_ranges.keys():
    df_total = globals()[f"businessActivity2024_{name}_total"]
    
    # Format date range
    start_str, end_str = event_date_ranges[name]
    start_fmt = datetime.strptime(start_str, "%Y-%m-%d").strftime("%B %d, %Y")
    end_fmt = datetime.strptime(end_str, "%Y-%m-%d").strftime("%B %d, %Y")
    event_period = f"{start_fmt} - {end_fmt}"
    
    # Optional: vertical markers
    verticals = vertical_date_labels.get(name, {})
    
    tabs.append(
        TabPanel(
            child=get_line_plot(
                df_total,
                event_period,
                "Source: Data for Good, Meta",
                subtitle=f"National average during {title_map[name]} compared to 45 days prior baseline",
                vertical_dates=verticals.get("dates"),
                vertical_labels=verticals.get("labels"),
                limitations_note="This dataset uses data about posting activity on Facebook to measure how local businesses are affected by and recover from crisis events. The methodology assumes businesses post more when open, which may not always be accurate."
            ),
            title=f"{title_map[name]}"
        )
    )

# Add manual "How to read it?" tab
tabs.append(
    TabPanel(
        child=column(
            Div(text="<h2>How to read it?</h2>"),
            Div(text="""
                <p>This chart visualizes <strong>Business Activity Trends</strong> during crisis events in India compared to a 45-day pre-crisis baseline.</p>
                <ul>
                  <li>A value of <strong>0.5</strong> represents <em>normal</em> or <em>baseline-like</em> activity levels.</li>
                  <li>Values <strong>above 0.5</strong> indicate increased business activity.</li>
                  <li>Values <strong>below 0.5</strong> indicate decreased business activity.</li>
                </ul>
                <p>The dashed line at 0.5 marks the baseline. Each line represents a business vertical.</p>
            """)
        ),
        title="How to read it?"
    )
)

# Display all tabs
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)


Loading BokehJS ...

### Analyzing Changes in Business Activity by Region 

In [130]:
# Merge 
businessActivity2024["polygon_name"] = businessActivity2024["polygon_name"].str.upper()
businessActivity2024["key"] = 1
ind_adm2["key"] = 1
ind_adm2["polygon_name"] = ind_adm2["polygon_name"].str.upper()

merged = pd.merge(
    ind_adm2.drop(columns=["geometry"]),
    businessActivity2024,
    on=["key", "polygon_name"],
    how="inner"
)

merged = pd.merge(
    merged,
    ind_adm2[["polygon_name", "geometry"]],
    on="polygon_name",
    how="left"
)

# Convert to GeoDataFrame
merged_gdf = gpd.GeoDataFrame(merged, geometry="geometry", crs=ind_adm2.crs)

event_date_ranges = {
    "Monsoon": ("2024-05-09", "2024-05-26"),
    "Cyclone_Remal": ("2024-05-24", "2024-06-10"),
    "Landslides_Kerala": ("2024-07-25", "2024-08-10"),
    "Flooding_Aug_Sept": ("2024-08-10", "2024-09-30"),
    "Cyclone_Dana": ("2024-10-20", "2024-11-13"),
    "Cyclone_Fengal": ("2024-12-02", "2024-12-16")
}

for name, (start, end) in event_date_ranges.items():
    mask = (merged_gdf['ds'] >= pd.to_datetime(start)) & (merged_gdf['ds'] <= pd.to_datetime(end))
    globals()[f"ind_adm2_merged_{name}"] = merged_gdf[mask].copy()




In [131]:
def map_plot(data, date=None, column_name="activity_quantile", title=None, source=None, subtitle=None):
    # Get districts with data for the date
    if date:
        data_for_date = data[data["ds"] == date]
    else:
        data_for_date = data

    background = ind_adm2.copy()

    # Set up color scale
    cmap = cm.RdYlGn if column_name == "activity_quantile" else cm.Reds
    norm = TwoSlopeNorm(vmin=0, vcenter=0.5, vmax=1) if column_name == "activity_quantile" else Normalize(vmin=0, vmax=data_for_date[column_name].max())

    fig, ax = plt.subplots(figsize=(7, 6))  # Slightly taller for full India

    # Plot full boundaries in light gray
    background.boundary.plot(ax=ax, linewidth=0.5, color="lightgray")

    # Plot active districts with data
    data_for_date.plot(
        column=column_name,
        cmap=cmap,
        norm=norm,
        linewidth=0.8,
        ax=ax,
        edgecolor="white",
        legend=True,
        legend_kwds={"label": column_name.replace("_", " ").title(), "orientation": "vertical"},
    )

    # Add title/subtitle/source
    if title:
        ax.set_title(title, fontsize=14, fontweight="bold")
    if subtitle:
        fig.text(0.5, 0.93, subtitle, ha='center', fontsize=12, style='italic')
    if source:
        fig.text(0.5, 0.01, source, ha='center', fontsize=10, style='italic')

    ax.axis("off")
    buf = BytesIO()
    plt.savefig(buf, format="png", bbox_inches="tight")
    plt.close(fig)
    buf.seek(0)

    return base64.b64encode(buf.read()).decode("utf-8")


### 🗺️ Analysis by Event and Region

The following maps present the analysis at **Admin Level 2** for each event.

For each event, the maps include:
- A **summary of key dates** and impacts,
- **Relevant links** to external sources or reports,
- A **map showing total business activity** during the event period.

These visualizations aim to provide a localized view of how business activity was affected across different regions during key crisis events.

#### Cyclone Remal Business Activity Trends Dataset

This map visualizes **business activity trends** following **Monsoon Study**, providing insights into economic disruptions and recovery in affected areas in this season.


In [132]:
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize, TwoSlopeNorm
import matplotlib.cm as cm
from io import BytesIO
import base64
from bokeh.io import show
from bokeh.models import Div, Panel, Tabs
from bokeh.layouts import column
from bokeh.plotting import output_notebook

# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> during India's Monsoon season compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-05-09", "2024-05-13", "2024-05-17", "2024-05-21", "2024-05-26"]
data_source = ind_adm2_merged_Monsoon  # Replace with actual data source

# Create tabs list
tabs = []


# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline."
            ),
            title=f"({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)



Loading BokehJS ...

#### Cyclone Remal Business Activity Trends Dataset (India)

This map visualizes **business activity trends** following **Cyclone Remal**.

**Key Insights from Cyclone Remal (May–June 2024)**

Cyclone Remal made landfall on **May 26, 2024**, near the coasts of **West Bengal (India)** and **Bangladesh**, bringing **strong winds**, **heavy rainfall**, and **storm surges**. The storm affected **infrastructure, power lines**, and **local businesses**, particularly in **coastal West Bengal**.

**Key Dates:**
- **May 26, 2024**: Cyclone Remal made landfall near **West Bengal**, India.
- **May 27, 2024**: High winds and flooding caused disruptions to transportation and electricity in **Kolkata and surrounding areas**.

**Key Places Affected:**
- **West Bengal**: Including **Kolkata**, **South 24 Parganas**, and **North 24 Parganas**, where homes, roads, and power lines were damaged.
- **Eastern India (coastal zones)**: Experienced temporary **power outages** and **transport disruption** due to flooding and fallen trees.

*Sources: 
- [Reuters – Cyclone Remal](https://www.reuters.com/world/asia-pacific/millions-without-power-cyclone-remal-pounds-bangladesh-india-2024-05-27/)
- [ReliefWeb – Cyclone Remal](https://reliefweb.int/report/india/ihh-sitrep-001-cyclone-remal)


In [133]:
import matplotlib.pyplot as plt
from matplotlib.colors import Normalize, TwoSlopeNorm
import matplotlib.cm as cm
from io import BytesIO
import base64
from bokeh.io import show
from bokeh.models import Div, Panel, Tabs
from bokeh.layouts import column
from bokeh.plotting import output_notebook

# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> after Cyclone Remal  compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-05-27","2024-05-28", "2024-05-29", "2024-06-02", "2024-06-06"]
data_source = ind_adm2_merged_Cyclone_Remal  # Replace with actual data source

# Create tabs list
tabs = []


# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline."
            ),
            title=f"({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)

Loading BokehJS ...

#### Landslides in Kerala – Business Activity Trends Dataset

This map visualizes **business activity trends** following the devastating **landslides in Kerala** in July 2024, offering insights into economic disruptions and recovery patterns across affected regions.
In late July 2024, **intense monsoon rains** triggered landslides in Kerala, particularly in the **Wayanad** and **Kozhikode** districts. 

**Key Dates:**
- **July 29–30, 2024**: Heavy rainfall led to multiple landslides in Wayanad and Kozhikode districts.

**Key Places Affected:**
- **Wayanad District**: Villages such as **Mundakkai**, **Chooralmala**,**Attamala**, **Meppadi** experienced severe landslides with extensive damage and casualties.
- **Kozhikode District**: The **Vilangad** area witnessed landslides that destroyed homes and displaced residents.

**Sources:**
- [Eos – The Landslide Blog](https://eos.org/thelandslideblog/wayanad-landslides)
- [ReliefWeb – Situation Report](https://reliefweb.int/report/india/local-situation-report-0092024-landslide-kerala-july-30-2024)
- [Reuters](https://www.reuters.com/world/india/washed-away-2024-08-16/)


In [134]:
# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> after the Landslides in Kerala compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-07-30", "2024-07-31","2024-08-01", "2024-08-02", "2024-08-06", "2024-08-10"]
data_source = ind_adm2_merged_Landslides_Kerala  # Replace with actual data source

# Create tabs list
tabs = []


# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline."
            ),
            title=f"({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)

Loading BokehJS ...

#### August–September 2024 Flooding in India: Business Activity Trends

This section presents **business activity trends** during the widespread flooding events across India in August and September 2024. The maps help visualize economic disruptions and patterns of recovery in the most affected areas.

**Key Dates**

- **Late August 2024**: Cyclone Asna formed over Gujarat and Madhya Pradesh, triggering heavy rainfall and flooding across Gujarat.
- **August 31 – September 9, 2024**: Intense flooding occurred in **Vijayawada, Andhra Pradesh**.
- **Mid-September 2024**: Severe floods hit **West Bengal**, particularly in the districts of **Ghatal** and **Udaynarayanpur**.

**Key Affected Regions**

- **Gujarat**: Districts such as **Vadodara**, **Jamnagar**, and **Rajkot** experienced flooding from Cyclone Asna, with major damage to infrastructure and agriculture.
- **Andhra Pradesh**: **Vijayawada** was heavily impacted by floods, with widespread disruptions to transport, housing, and livelihoods.
- **West Bengal**: Areas including **Howrah**, **Hooghly**, and **Paschim Medinipur** were significantly affected, with damage to homes, roads, and crop fields.

**Sources**

- [2024 South Asia Floods - Center for Disaster Philanthropy​ Center for Disaster Philanthropy](https://disasterphilanthropy.org/disasters/2024-south-asia-floods/)
- [Reliefweb - India: Floods and Landslides](https://reliefweb.int/disaster/fl-2024-000109-ind)


In [135]:
# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> after the flooding events across India in August and September 2024 compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-08-10", "2024-08-22", "2024-09-04", "2024-09-17", "2024-09-30"]
data_source = ind_adm2_merged_Flooding_Aug_Sept  # Replace with actual data source

# Create tabs list
tabs = []


# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline."
            ),
            title=f"({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)

Loading BokehJS ...

#### Cyclone Dana Business Activity Trends Dataset

This section presents **business activity trends** during **Cyclone Dana**, highlighting economic disruptions and recovery patterns in the affected areas.

** Key Dates**

- **October 22, 2024**: Cyclone Dana intensified into a severe cyclonic storm over the Bay of Bengal.  
- **October 24–25, 2024**: Made landfall between **Puri (Odisha)** and **Sagar Island (West Bengal)** with wind speeds up to 120 km/h.  
- **October 26, 2024**: Weakened into a depression and dissipated over northern Odisha.

**Key Affected Regions**

- **Odisha**: Districts such as **Bhadrak**, **Kendrapara**, and **Balasore** experienced uprooted trees, power outages, and road blockages.  
- **West Bengal**: Coastal areas faced heavy rainfall and strong winds, leading to infrastructure damage and agricultural losses.

**Sources**

- [Reuters – Cyclone Dana impact](https://www.reuters.com/business/environment/how-has-cyclone-dana-impacted-life-indias-eastern-coast-2024-10-25/)
- [India Meteorological Department (IMD) Bulletin – Nov 7, 2024](https://internal.imd.gov.in/press_release/20241107_pr_3389.pdf)
- [ReliefWeb – India: Floods and Landslides (Jul–Nov 2024)](https://reliefweb.int/disaster/fl-2024-000109-ind)


In [136]:
# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> after Cyclone Dana compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-10-22", "2024-10-24", "2024-10-26", "2024-10-28","2024-10-29", "2024-10-30", "2024-11-02"]
data_source = ind_adm2_merged_Cyclone_Dana  # Replace with actual data source

# Create tabs list
tabs = []


# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline."
            ),
            title=f"({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)

Loading BokehJS ...

#### Cyclone Fengal Business Activity Trends Dataset

This section presents **business activity trends** during **Cyclone Fengal**, highlighting economic disruptions and recovery patterns in the affected areas.

**Key Dates**

- **November 25, 2024**: Formation of a low-pressure area over the Bay of Bengal.  
- **November 29, 2024**: Intensified into Cyclonic Storm Fengal.  
- **November 30, 2024**: Made landfall between Karaikal and Mamallapuram near Puducherry.  
- **December 1, 2024**: Weakened into a depression over Tamil Nadu.  
- **December 4, 2024**: Dissipated over the Arabian Sea.

**Key Affected Regions**

- **Tamil Nadu**: Districts like Chennai, Tiruvannamalai, Villupuram, and Vellore experienced severe flooding, landslides, and infrastructure damage.  
- **Puducherry**: Significant rainfall led to urban flooding and disruptions in daily activities.  
- **Andhra Pradesh & Kerala**: Heavy rainfall caused localized flooding and agricultural losses.

**Sources**

- [India Meteorological Department Bulletin – November 30, 2024](https://internal.imd.gov.in/press_release/20241130_pr_3442.pdf)  
- [GDACS Report on Cyclone Fengal](https://www.gdacs.org/report.aspx?episodeid=7&eventid=1001130&eventtype=TC)   
- [ReliefWeb – Tropical Cyclone Fengal](https://reliefweb.int/disaster/tc-2024-000219-lka)

In [137]:
# Activate notebook output
output_notebook()

# Function to generate a Bokeh tab for maps
def get_map_tab(data, date=None, title=None, source=None, subtitle=None, column_name="activity_quantile"):
    """Create a tab with a static map image and optional tooltip information."""
    img_base64 = map_plot(data, date, column_name)

    title_div = Div(text=f"<h2>{title}</h2>", styles={"text-align": "left", "font-size": "14pt", "font-weight": "bold"})
    subtitle_div = Div(text=f"<p><em>{subtitle}</em></p>" if subtitle else "", styles={"text-align": "left", "font-size": "12pt", "margin-bottom": "10px"})
    source_div = Div(text=f"<p><small>{source}</small></p>", styles={"text-align": "left", "font-size": "12pt", "margin-top": "10px"})

    img_tag = f'<img src="data:image/png;base64,{img_base64}" width="800">'
    img_div = Div(text=img_tag)

    layout = column(title_div, subtitle_div, img_div, source_div)

    return layout

# Function to create explanation tab
def get_explanation_tab():
    """Create a tab explaining how to read the map."""
    title_div = Div(text="<h2>How to read it?</h2>", styles={"text-align": "left", "font-size": "18pt", "font-weight": "bold"})
    explanation_div = Div(text="""
        <p>This map visualizes <strong>Business Activity Trends</strong> after Cyclone Fengal compared to a 45-day pre-crisis baseline.</p>
        <ul>
          <li>The tabs show <em>Activity Quantile</em>, measuring business activity relative to the baseline.</li>
          <li>Values <strong>above 0.5</strong> indicate increased activity; <strong>below 0.5</strong> indicate decreased activity in relation to the baseline date.</li>
        </ul>
        <hr>
        <p>This dataset is based on social media business posting activity.</p>
    """, styles={"text-align": "left", "font-size": "12pt"})

    return column(title_div, explanation_div)

# Define selected dates for business activity
selected_dates = ["2024-12-02", "2024-12-04", "2024-12-06", "2024-12-10", "2024-12-13"]
data_source = ind_adm2_merged_Cyclone_Fengal  # Replace with actual data source

# Create tabs list
tabs = []


# Add multiple Business Activity maps for selected dates
for date in selected_dates:
    tabs.append(
        TabPanel(
            child=get_map_tab(
                data_source,
                date=date,
                title=f"Business Activity on {date}",
                source="Source: Data for Good, Meta",
                subtitle="Compared to the 45-day prior baseline."
            ),
            title=f"({date})"
        )
    )

# Add the explanation tab
tabs.append(TabPanel(child=get_explanation_tab(), title="How to read it?"))

# Create Bokeh Tabs layout
tabs_layout = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs_layout)

Loading BokehJS ...